In [0]:
from pyspark import SparkContext
from pyspark.sql import SparkSession

# Initialize SparkSession
spark = SparkSession.builder.appName("TestApp").getOrCreate()

In [0]:
options = {
    "header": True,              # CSV file has header
    "inferSchema": True,         # Infer schema
    "mode": "DROPMALFORMED"      # Drop rows with malformed data
}

coffee_df = spark.read.csv("dbfs:/FileStore/shared_uploads/mkmeetakapoor@gmail.com/source/coffee_ratings.csv", **options)

# Show the DataFrame schema
coffee_df.printSchema()

# Show the first few rows of the DataFrame
display(coffee_df.take(5))

root
 |-- total_cup_points: string (nullable = true)
 |-- species: string (nullable = true)
 |-- owner: string (nullable = true)
 |-- country_of_origin: string (nullable = true)
 |-- farm_name: string (nullable = true)
 |-- lot_number: string (nullable = true)
 |-- mill: string (nullable = true)
 |-- ico_number: string (nullable = true)
 |-- company: string (nullable = true)
 |-- altitude: string (nullable = true)
 |-- region: string (nullable = true)
 |-- producer: string (nullable = true)
 |-- number_of_bags: integer (nullable = true)
 |-- bag_weight: string (nullable = true)
 |-- in_country_partner: string (nullable = true)
 |-- harvest_year: string (nullable = true)
 |-- grading_date: string (nullable = true)
 |-- owner_1: string (nullable = true)
 |-- variety: string (nullable = true)
 |-- processing_method: string (nullable = true)
 |-- aroma: double (nullable = true)
 |-- flavor: double (nullable = true)
 |-- aftertaste: double (nullable = true)
 |-- acidity: double (nullable = 

total_cup_points species owner country_of_origin farm_name lot_number mill ico_number company altitude region producer number_of_bags bag_weight in_country_partner harvest_year grading_date owner_1 variety processing_method aroma flavor aftertaste acidity body balance uniformity clean_cup sweetness cupper_points moisture category_one_defects quakers color category_two_defects expiration certification_body certification_address certification_contact unit_of_measurement altitude_low_meters altitude_high_meters altitude_mean_meters 90.58 Arabica metad plc Ethiopia metad plc NA metad plc 2014/2015 metad agricultural developmet plc 1950-2200 guji-hambela METAD PLC 300 60 kg METAD Agricultural Development plc 2014 April 4th, 2015 metad plc NA Washed / Wet 8.67 8.83 8.67 8.75 8.5 8.42 10.0 10.0 10.0 8.75 0.12 0 0 Green 0 April 3rd, 2016 METAD Agricultural Development plc 309fcf77415a3661ae83e027f7e5f05dad786e44 19fef5a731de2db57d16da10287413f5f99bc2dd m 1950 2200 2075 89.92 Arabica metad plc Ethiopia metad plc NA metad plc 2014/2015 metad agricultural developmet plc 1950-2200 guji-hambela METAD PLC 300 60 kg METAD Agricultural Development plc 2014 April 4th, 2015 metad plc Other Washed / Wet 8.75 8.67 8.5 8.58 8.42 8.42 10.0 10.0 10.0 8.58 0.12 0 0 Green 1 April 3rd, 2016 METAD Agricultural Development plc 309fcf77415a3661ae83e027f7e5f05dad786e44 19fef5a731de2db57d16da10287413f5f99bc2dd m 1950 2200 2075 89.75 Arabica grounds for health admin Guatemala "san marcos barrancas ""san cristobal cuch" NA NA NA NA 1600 - 1800 m NA NA 5 1 Specialty Coffee Association NA May 31st, 2010 Grounds for Health Admin Bourbon NA 8.42 8.5 8.42 8.42 8.33 8.42 10.0 10.0 10.0 9.25 0.0 0 0 NA 0 May 31st, 2011 Specialty Coffee Association 36d0d00a3724338ba7937c52a378d085f2172daa 0878a7d4b9d35ddbf0fe2ce69a2062cceb45a660 m 1600 1800 1700 89 Arabica yidnekachew dabessa Ethiopia yidnekachew dabessa coffee plantation NA wolensu NA yidnekachew debessa coffee plantation 1800-2200 oromia Yidnekachew Dabessa Coffee Plantation 320 60 kg METAD Agricultural Development plc 2014 March 26th, 2015 Yidnekachew Dabessa NA Natural / Dry 8.17 8.58 8.42 8.42 8.5 8.25 10.0 10.0 10.0 8.67 0.11 0 0 Green 2 March 25th, 2016 METAD Agricultural Development plc 309fcf77415a3661ae83e027f7e5f05dad786e44 19fef5a731de2db57d16da10287413f5f99bc2dd m 1800 2200 2000 88.83 Arabica metad plc Ethiopia metad plc NA metad plc 2014/2015 metad agricultural developmet plc 1950-2200 guji-hambela METAD PLC 300 60 kg METAD Agricultural Development plc 2014 April 4th, 2015 metad plc Other Washed / Wet 8.25 8.5 8.25 8.5 8.42 8.33 10.0 10.0 10.0 8.58 0.12 0 0 Green 2 April 3rd, 2016 METAD Agricultural Development plc 309fcf77415a3661ae83e027f7e5f05dad786e44 19fef5a731de2db57d16da10287413f5f99bc2dd m 1950 2200 2075

Databricks visualization. Run in Databricks to view.

In [0]:
coffee_df.count()

Out[3]: 1346

In [0]:
coffee_df.distinct().count()

Out[4]: 1336

In [0]:
schema = coffee_df.schema

In [0]:
target_delta_table_path = "dbfs:/FileStore/mkmeetakapoor@gmail.com/target/"
source_path = "dbfs:/FileStore/shared_uploads/mkmeetakapoor@gmail.com/source/"

In [0]:
streamingAggregatesDF = spark.readStream.format("csv").schema(schema).option("basePath",source_path).load(source_path)

In [0]:
emptyRDD = spark.sparkContext.parallelize([])
targetDF = spark.createDataFrame(data = emptyRDD,
                           schema = schema)
targetDF.write.format("delta").mode("overwrite").save(target_delta_table_path)

In [0]:
from delta import *
target_table = DeltaTable.forPath(spark, target_delta_table_path)
display(target_table.toDF())
target_table.toDF().count()

total_cup_points species owner country_of_origin farm_name lot_number mill ico_number company altitude region producer number_of_bags bag_weight in_country_partner harvest_year grading_date owner_1 variety processing_method aroma flavor aftertaste acidity body balance uniformity clean_cup sweetness cupper_points moisture category_one_defects quakers color category_two_defects expiration certification_body certification_address certification_contact unit_of_measurement altitude_low_meters altitude_high_meters altitude_mean_meters total_cup_points species owner country_of_origin farm_name lot_number mill ico_number company altitude region producer null bag_weight in_country_partner harvest_year grading_date owner_1 variety processing_method null null null null null null null null null null null null quakers color null expiration certification_body certification_address certification_contact unit_of_measurement altitude_low_meters altitude_high_meters altitude_mean_meters 90.58 Arabica metad plc Ethiopia metad plc NA metad plc 2014/2015 metad agricultural developmet plc 1950-2200 guji-hambela METAD PLC 300 60 kg METAD Agricultural Development plc 2014 April 4th, 2015 metad plc NA Washed / Wet 8.67 8.83 8.67 8.75 8.5 8.42 10.0 10.0 10.0 8.75 0.12 0 0 Green 0 April 3rd, 2016 METAD Agricultural Development plc 309fcf77415a3661ae83e027f7e5f05dad786e44 19fef5a731de2db57d16da10287413f5f99bc2dd m 1950 2200 2075 89.92 Arabica metad plc Ethiopia metad plc NA metad plc 2014/2015 metad agricultural developmet plc 1950-2200 guji-hambela METAD PLC 300 60 kg METAD Agricultural Development plc 2014 April 4th, 2015 metad plc Other Washed / Wet 8.75 8.67 8.5 8.58 8.42 8.42 10.0 10.0 10.0 8.58 0.12 0 0 Green 1 April 3rd, 2016 METAD Agricultural Development plc 309fcf77415a3661ae83e027f7e5f05dad786e44 19fef5a731de2db57d16da10287413f5f99bc2dd m 1950 2200 2075 89.75 Arabica grounds for health admin Guatemala "san marcos barrancas ""san cristobal cuch" NA NA NA NA 1600 - 1800 m NA NA 5 1 Specialty Coffee Association NA May 31st, 2010 Grounds for Health Admin Bourbon NA 8.42 8.5 8.42 8.42 8.33 8.42 10.0 10.0 10.0 9.25 0.0 0 0 NA 0 May 31st, 2011 Specialty Coffee Association 36d0d00a3724338ba7937c52a378d085f2172daa 0878a7d4b9d35ddbf0fe2ce69a2062cceb45a660 m 1600 1800 1700 89 Arabica yidnekachew dabessa Ethiopia yidnekachew dabessa coffee plantation NA wolensu NA yidnekachew debessa coffee plantation 1800-2200 oromia Yidnekachew Dabessa Coffee Plantation 320 60 kg METAD Agricultural Development plc 2014 March 26th, 2015 Yidnekachew Dabessa NA Natural / Dry 8.17 8.58 8.42 8.42 8.5 8.25 10.0 10.0 10.0 8.67 0.11 0 0 Green 2 March 25th, 2016 METAD Agricultural Development plc 309fcf77415a3661ae83e027f7e5f05dad786e44 19fef5a731de2db57d16da10287413f5f99bc2dd m 1800 2200 2000 88.83 Arabica metad plc Ethiopia metad plc NA metad plc 2014/2015 metad agricultural developmet plc 1950-2200 guji-hambela METAD PLC 300 60 kg METAD Agricultural Development plc 2014 April 4th, 2015 metad plc Other Washed / Wet 8.25 8.5 8.25 8.5 8.42 8.33 10.0 10.0 10.0 8.58 0.12 0 0 Green 2 April 3rd, 2016 METAD Agricultural Development plc 309fcf77415a3661ae83e027f7e5f05dad786e44 19fef5a731de2db57d16da10287413f5f99bc2dd m 1950 2200 2075 88.83 Arabica ji-ae ahn Brazil NA NA NA NA NA NA NA NA 100 30 kg Specialty Coffee Institute of Asia 2013 September 3rd, 2013 Ji-Ae Ahn NA Natural / Dry 8.58 8.42 8.42 8.5 8.25 8.33 10.0 10.0 10.0 8.33 0.11 0 0 Bluish-Green 1 September 3rd, 2014 Specialty Coffee Institute of Asia 726e4891cf2c9a4848768bd34b668124d12c4224 b70da261fcc84831e3e9620c30a8701540abc200 m NA NA NA 88.75 Arabica hugo valdivia Peru NA NA hvc NA richmond investment-coffee department NA NA HVC 100 69 kg Specialty Coffee Institute of Asia 2012 September 17th, 2012 Hugo Valdivia Other Washed / Wet 8.42 8.5 8.33 8.5 8.25 8.25 10.0 10.0 10.0 8.5 0.11 0 0 Bluish-Green 0 September 17th, 2013 Specialty Coffee Institute of Asia 726e4891cf2c9a4848768bd34b668124d12c4224 b70da261fcc84831e3e9620c30

Out[13]: 1347

In [0]:
display(target_table.toDF())

total_cup_points species owner country_of_origin farm_name lot_number mill ico_number company altitude region producer number_of_bags bag_weight in_country_partner harvest_year grading_date owner_1 variety processing_method aroma flavor aftertaste acidity body balance uniformity clean_cup sweetness cupper_points moisture category_one_defects quakers color category_two_defects expiration certification_body certification_address certification_contact unit_of_measurement altitude_low_meters altitude_high_meters altitude_mean_meters total_cup_points species owner country_of_origin farm_name lot_number mill ico_number company altitude region producer null bag_weight in_country_partner harvest_year grading_date owner_1 variety processing_method null null null null null null null null null null null null quakers color null expiration certification_body certification_address certification_contact unit_of_measurement altitude_low_meters altitude_high_meters altitude_mean_meters 90.58 Arabica metad plc Ethiopia metad plc NA metad plc 2014/2015 metad agricultural developmet plc 1950-2200 guji-hambela METAD PLC 300 60 kg METAD Agricultural Development plc 2014 April 4th, 2015 metad plc NA Washed / Wet 8.67 8.83 8.67 8.75 8.5 8.42 10.0 10.0 10.0 8.75 0.12 0 0 Green 0 April 3rd, 2016 METAD Agricultural Development plc 309fcf77415a3661ae83e027f7e5f05dad786e44 19fef5a731de2db57d16da10287413f5f99bc2dd m 1950 2200 2075 89.92 Arabica metad plc Ethiopia metad plc NA metad plc 2014/2015 metad agricultural developmet plc 1950-2200 guji-hambela METAD PLC 300 60 kg METAD Agricultural Development plc 2014 April 4th, 2015 metad plc Other Washed / Wet 8.75 8.67 8.5 8.58 8.42 8.42 10.0 10.0 10.0 8.58 0.12 0 0 Green 1 April 3rd, 2016 METAD Agricultural Development plc 309fcf77415a3661ae83e027f7e5f05dad786e44 19fef5a731de2db57d16da10287413f5f99bc2dd m 1950 2200 2075 89.75 Arabica grounds for health admin Guatemala "san marcos barrancas ""san cristobal cuch" NA NA NA NA 1600 - 1800 m NA NA 5 1 Specialty Coffee Association NA May 31st, 2010 Grounds for Health Admin Bourbon NA 8.42 8.5 8.42 8.42 8.33 8.42 10.0 10.0 10.0 9.25 0.0 0 0 NA 0 May 31st, 2011 Specialty Coffee Association 36d0d00a3724338ba7937c52a378d085f2172daa 0878a7d4b9d35ddbf0fe2ce69a2062cceb45a660 m 1600 1800 1700 89 Arabica yidnekachew dabessa Ethiopia yidnekachew dabessa coffee plantation NA wolensu NA yidnekachew debessa coffee plantation 1800-2200 oromia Yidnekachew Dabessa Coffee Plantation 320 60 kg METAD Agricultural Development plc 2014 March 26th, 2015 Yidnekachew Dabessa NA Natural / Dry 8.17 8.58 8.42 8.42 8.5 8.25 10.0 10.0 10.0 8.67 0.11 0 0 Green 2 March 25th, 2016 METAD Agricultural Development plc 309fcf77415a3661ae83e027f7e5f05dad786e44 19fef5a731de2db57d16da10287413f5f99bc2dd m 1800 2200 2000 88.83 Arabica metad plc Ethiopia metad plc NA metad plc 2014/2015 metad agricultural developmet plc 1950-2200 guji-hambela METAD PLC 300 60 kg METAD Agricultural Development plc 2014 April 4th, 2015 metad plc Other Washed / Wet 8.25 8.5 8.25 8.5 8.42 8.33 10.0 10.0 10.0 8.58 0.12 0 0 Green 2 April 3rd, 2016 METAD Agricultural Development plc 309fcf77415a3661ae83e027f7e5f05dad786e44 19fef5a731de2db57d16da10287413f5f99bc2dd m 1950 2200 2075 88.83 Arabica ji-ae ahn Brazil NA NA NA NA NA NA NA NA 100 30 kg Specialty Coffee Institute of Asia 2013 September 3rd, 2013 Ji-Ae Ahn NA Natural / Dry 8.58 8.42 8.42 8.5 8.25 8.33 10.0 10.0 10.0 8.33 0.11 0 0 Bluish-Green 1 September 3rd, 2014 Specialty Coffee Institute of Asia 726e4891cf2c9a4848768bd34b668124d12c4224 b70da261fcc84831e3e9620c30a8701540abc200 m NA NA NA 88.75 Arabica hugo valdivia Peru NA NA hvc NA richmond investment-coffee department NA NA HVC 100 69 kg Specialty Coffee Institute of Asia 2012 September 17th, 2012 Hugo Valdivia Other Washed / Wet 8.42 8.5 8.33 8.5 8.25 8.25 10.0 10.0 10.0 8.5 0.11 0 0 Bluish-Green 0 September 17th, 2013 Specialty Coffee Institute of Asia 726e4891cf2c9a4848768bd34b668124d12c4224 b70da261fcc84831e3e9620c30

In [0]:
from delta.tables import *

deltaTable = DeltaTable.forPath(spark, target_delta_table_path)

# Function to upsert microBatchOutputDF into Delta table using merge
def upsertToDelta(microBatchOutputDF, batchId):
  (deltaTable.alias("t").merge(
      microBatchOutputDF.alias("s"),
      "s.country_of_origin = t.country_of_origin")
    .whenMatchedDelete()
    .whenNotMatchedInsertAll()
    .execute()
  )

# Write the output of a streaming aggregation query into Delta table
(streamingAggregatesDF.writeStream
  .format("delta")
  .foreachBatch(upsertToDelta)
  .outputMode("update")
  .start()
)


Out[15]: <pyspark.sql.streaming.query.StreamingQuery at 0x7f6382049b20>

In [0]:
from delta import *
target_table = DeltaTable.forPath(spark, target_delta_table_path)
display(target_table.toDF())

total_cup_points species owner country_of_origin farm_name lot_number mill ico_number company altitude region producer number_of_bags bag_weight in_country_partner harvest_year grading_date owner_1 variety processing_method aroma flavor aftertaste acidity body balance uniformity clean_cup sweetness cupper_points moisture category_one_defects quakers color category_two_defects expiration certification_body certification_address certification_contact unit_of_measurement altitude_low_meters altitude_high_meters altitude_mean_meters ",KlemOrganics,Catuai,Natural / Dry,7.5,7.58,7.5,7.5,7.75,7.83,9.33,9.33,9.33,7.58,0.11,0,0,Green,0,"November 15th 2018 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null ,Specialty Coffee Association,d3ed2a8c1db69c87daef88f425dd0e8ef3216a39,0878a7d4b9d35ddbf0fe2ce69a2062cceb45a660,m,1100,1100,1100
 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null ",2013/2014,"December 26th 2013 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null ","CQI Taiwan ICP CQI台灣合作夥伴 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null ",Typica,Washed / Wet,7.25,7.25,7.17,7.25,7.25,7.25,10,10,10,7,0.11,0,0,Green,0,"December 26th 2014" Blossom Valley International
 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null ,09e3c859cac41901d54f4bd36cce80d19c9272f5,94828eb00127a1563ed640ea428f42f3313b182d,m,600,600,600
 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null ",KlemOrganics,Catuai,Natural / Dry,7.5,7.58,7.5,7.5,7.75,7.83,9.33,9.33,9.33,7.58,0.11,0,0,Green,0,"November 15th 2018 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null ,Specialty Coffee Association,d3ed2a8c1db69c87daef88f425dd0e8ef3216a39,0878a7d4b9d35ddbf0fe2ce69a2062cceb45a660,m,1100,1100,1100
 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null ",2013/2014,"December 26th 2013 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null ","CQI Taiwan ICP CQI台灣合作夥伴 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null ",Typica,Washed / Wet,7.25,7.25,7.17,7.25,7.25,7.25,10,10,10,7,0.11,0,0,Green,0,"December 26th 2014" Blossom Valley International
 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null ,09e3c859cac41901d54f4bd36cce80d19c9272f5,94828eb00127a1563ed640ea428f42f3313b182d,m,600,600,600
 null null null null null null null null null null null null null null null null null null null null null null null nu

In [0]:
display(target_table.history())

version timestamp userId userName operation operationParameters job notebook clusterId readVersion isolationLevel isBlindAppend operationMetrics userMetadata engineInfo 3 2024-05-02T03:28:08.000+0000 4342349583766340 mkmeetakapoor@gmail.com WRITE Map(mode -> Overwrite, partitionBy -> []) null List(1093230493569748) 0502-022405-ahk7wt5u 2 WriteSerializable false Map(numFiles -> 0, numOutputRows -> 0, numOutputBytes -> 0) null Databricks-Runtime/12.2.x-scala2.12 2 2024-05-02T03:19:43.000+0000 4342349583766340 mkmeetakapoor@gmail.com MERGE Map(predicate -> ["(certification_address#433 = certification_address#5851)"], matchedPredicates -> [{"actionType":"delete"}], notMatchedPredicates -> [{"actionType":"insert"}], notMatchedBySourcePredicates -> []) null List(1093230493569748) 0502-022405-ahk7wt5u 1 WriteSerializable false Map(numTargetRowsCopied -> 10, numTargetRowsDeleted -> 202811, numTargetFilesAdded -> 2, numTargetBytesAdded -> 25136, numTargetBytesRemoved -> 142860, numTargetDeletionVectorsAdded -> 0, numTargetRowsMatchedUpdated -> 0, executionTimeMs -> 11380, numTargetRowsInserted -> 10, numTargetRowsMatchedDeleted -> 202811, scanTimeMs -> 4496, numTargetRowsUpdated -> 0, numOutputRows -> 20, numTargetDeletionVectorsRemoved -> 0, numTargetRowsNotMatchedBySourceUpdated -> 0, numTargetChangeFilesAdded -> 0, numSourceRows -> 1347, numTargetFilesRemoved -> 1, numTargetRowsNotMatchedBySourceDeleted -> 0, rewriteTimeMs -> 5640) null Databricks-Runtime/12.2.x-scala2.12 1 2024-05-02T03:18:18.000+0000 4342349583766340 mkmeetakapoor@gmail.com MERGE Map(predicate -> ["(certification_address#433 = certification_address#3256)"], matchedPredicates -> [{"actionType":"delete"}], notMatchedPredicates -> [{"actionType":"insert"}], notMatchedBySourcePredicates -> []) null List(1093230493569748) 0502-022405-ahk7wt5u 0 WriteSerializable false Map(numTargetRowsCopied -> 0, numTargetRowsDeleted -> 0, numTargetFilesAdded -> 1, numTargetBytesAdded -> 142860, numTargetBytesRemoved -> 0, numTargetDeletionVectorsAdded -> 0, numTargetRowsMatchedUpdated -> 0, executionTimeMs -> 10638, numTargetRowsInserted -> 1347, numTargetRowsMatchedDeleted -> 0, scanTimeMs -> 3892, numTargetRowsUpdated -> 0, numOutputRows -> 1347, numTargetDeletionVectorsRemoved -> 0, numTargetRowsNotMatchedBySourceUpdated -> 0, numTargetChangeFilesAdded -> 0, numSourceRows -> 1347, numTargetFilesRemoved -> 0, numTargetRowsNotMatchedBySourceDeleted -> 0, rewriteTimeMs -> 5036) null Databricks-Runtime/12.2.x-scala2.12 0 2024-05-02T03:17:23.000+0000 4342349583766340 mkmeetakapoor@gmail.com WRITE Map(mode -> Overwrite, partitionBy -> []) null List(1093230493569748) 0502-022405-ahk7wt5u null WriteSerializable false Map(numFiles -> 0, numOutputRows -> 0, numOutputBytes -> 0) null Databricks-Runtime/12.2.x-scala2.12